In [ ]:
from google.colab import drive
drive.flush_and_unmount()


Drive not mounted, so nothing to flush and unmount.


In [ ]:
import os
import pandas as pd
import json
from PIL import Image
import matplotlib.pyplot as plt
import zipfile

zip_path = '/content/drive/MyDrive/datafiles.zip'
base_path = '/content/drive/MyDrive/datas/'

# Cria a pasta base se ela não existir
if not os.path.exists(base_path):
    os.makedirs(base_path)

# Extrair o conteúdo do arquivo zip
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(base_path)

# Listar as pastas extraídas
folders = [f for f in os.listdir(base_path) if os.path.isdir(os.path.join(base_path, f))]
print("Pastas extraídas:", folders)


Pastas extraídas: ['data']


In [ ]:
for folder in sorted(base_path):
    image_folder = os.path.join(base_path, folder, 'images')

    if os.path.exists(image_folder):
        images = [img for img in os.listdir(image_folder) if img.endswith('.jpg')]

        for image_file in images:
            img_path = os.path.join(image_folder, image_file)
            img = Image.open(img_path)

            plt.imshow(img)
            plt.axis('off')
            plt.show()


In [ ]:
import os
import pandas as pd
import json
from IPython.display import display

def process_json_files(base_path):
    all_data = []
    file_counts = {}
    total_count = 0

    for folder in sorted(os.listdir(base_path)):
        folder_path = os.path.join(base_path, folder)
        if os.path.isdir(folder_path):
            json_file = os.path.join(folder_path, 'result.json')
            if os.path.exists(json_file):
                with open(json_file, 'r') as f:
                    data = json.load(f)

                file_count = 0
                if 'images' in data and 'annotations' in data and 'categories' in data:

                    category_map = {cat['id']: cat['name'] for cat in data['categories']}
                    for img in data['images']:

                        for ann in data['annotations']:
                            if ann['image_id'] == img['id']:
                                row = {
                                    'row_number': len(all_data) + 1,
                                    'image_id': img['file_name'].split('\\')[-1].split('.')[0],
                                    'file_name': img['file_name'],
                                    'file_name_original': img['file_name'],
                                    'width': img['width'],
                                    'height': img['height'],
                                    'id': ann['id'],
                                    'category_id': ann['category_id'],
                                    'class_name': category_map.get(ann['category_id'], 'Unknown'),
                                    'bbox_0': ann['bbox'][0],
                                    'bbox_1': ann['bbox'][1],
                                    'bbox_2': ann['bbox'][2],
                                    'bbox_3': ann['bbox'][3]
                                }
                                all_data.append(row)
                                file_count += 1
                else:
                    print(f"Unexpected structure in {json_file}")

                file_counts[json_file] = file_count
                total_count += file_count
                print(f"Processed {file_count} annotations from {json_file}")

    print(f"Total processed annotations: {total_count}")
    df = pd.DataFrame(all_data)
    return df, file_counts, total_count

base_path = '/content/drive/MyDrive/datas/data'

df, file_counts, total_count = process_json_files(base_path)

def format_df(df):
    return (df.style
            .set_properties(**{
                'color': 'white',
                'border-color': 'white'
            })
            .set_table_styles([
                {'selector': 'th', 'props': [('background-color', '#696969'), ('color', 'white')]},
                {'selector': 'td', 'props': [('border', '1px solid white')]},
            ])
            .format({
                'bbox_0': '{:.6f}',
                'bbox_1': '{:.6f}',
                'bbox_2': '{:.6f}',
                'bbox_3': '{:.6f}'
            })
            .hide(axis="index")
           )

display(format_df(df))

print("\nAnnotations per file:")
for file, count in file_counts.items():
    print(f"{file}: {count} annotations")

print(f"\nTotal number of annotations: {total_count}")

# Função para salvar o DataFrame em um arquivo JSON
def save_df_to_json(df, output_path):
    # Converter DataFrame para JSON
    json_data = df.to_dict(orient='records')  # Converter cada linha para um dicionário

    # Escrever o JSON no arquivo
    with open(output_path, 'w') as json_file:
        json.dump(json_data, json_file, indent=4)

    print(f"JSON file saved to {output_path}")

# Caminho onde o arquivo JSON será salvo
output_json_path = '/content/drive/MyDrive/datas/annotations.json'

# Salvar o DataFrame em JSON
save_df_to_json(df, output_json_path)


Processed 155 annotations from /content/drive/MyDrive/datas/data/01/result.json
Processed 79 annotations from /content/drive/MyDrive/datas/data/02/result.json
Processed 132 annotations from /content/drive/MyDrive/datas/data/03/result.json
Processed 192 annotations from /content/drive/MyDrive/datas/data/04/result.json
Processed 127 annotations from /content/drive/MyDrive/datas/data/05/result.json
Processed 129 annotations from /content/drive/MyDrive/datas/data/06/result.json
Processed 131 annotations from /content/drive/MyDrive/datas/data/07/result.json
Processed 116 annotations from /content/drive/MyDrive/datas/data/08/result.json
Processed 121 annotations from /content/drive/MyDrive/datas/data/09/result.json
Processed 20 annotations from /content/drive/MyDrive/datas/data/10/result.json
Processed 142 annotations from /content/drive/MyDrive/datas/data/11/result.json
Processed 152 annotations from /content/drive/MyDrive/datas/data/12/result.json
Processed 246 annotations from /content/dr


Annotations per file:
/content/drive/MyDrive/datas/data/01/result.json: 155 annotations
/content/drive/MyDrive/datas/data/02/result.json: 79 annotations
/content/drive/MyDrive/datas/data/03/result.json: 132 annotations
/content/drive/MyDrive/datas/data/04/result.json: 192 annotations
/content/drive/MyDrive/datas/data/05/result.json: 127 annotations
/content/drive/MyDrive/datas/data/06/result.json: 129 annotations
/content/drive/MyDrive/datas/data/07/result.json: 131 annotations
/content/drive/MyDrive/datas/data/08/result.json: 116 annotations
/content/drive/MyDrive/datas/data/09/result.json: 121 annotations
/content/drive/MyDrive/datas/data/10/result.json: 20 annotations
/content/drive/MyDrive/datas/data/11/result.json: 142 annotations
/content/drive/MyDrive/datas/data/12/result.json: 152 annotations
/content/drive/MyDrive/datas/data/13/result.json: 246 annotations
/content/drive/MyDrive/datas/data/14/result.json: 140 annotations
/content/drive/MyDrive/datas/data/15/result.json: 165 a

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.patches as patches
from PIL import Image
import os
import json
import zipfile

def draw_bounding_boxes(img, annotations, image_id, category_map, color_map):
    fig, ax = plt.subplots(1, figsize=(12, 12))
    ax.imshow(img)

    for ann in annotations:
        if ann['image_id'] == image_id:
            bbox = ann['bbox']
            category = ann['category_id']
            color = color_map[category]
            rect = patches.Rectangle((bbox[0], bbox[1]), bbox[2], bbox[3],
                                     linewidth=2, edgecolor=color,
                                     facecolor='none')
            ax.add_patch(rect)

            plt.text(bbox[0], bbox[1], category_map[category],
                     color='white', fontweight='bold',
                     bbox=dict(facecolor=color, edgecolor='none', alpha=0.7))

    plt.axis('off')
    return fig

def remove_timestamp(filename):
    parts = filename.split('-', 1)
    new_filename = parts[1] if len(parts) > 1 else filename
    return new_filename

# Filtro para imagens
def is_valid_image(file_name):
    return file_name.endswith('.jpg') and "._" not in file_name

# Diretório base das pastas com imagens e JSONs
base_path = '/content/drive/MyDrive/datas/data'

color_map = {0: 'red', 1: 'blue', 2: 'green'}

total_images_processed = 0
processed_images = set()

# Diretório temporário para salvar as imagens anotadas
temp_dir = '/content/drive/MyDrive/datas/temp_annotated_images'

# Certifique-se de que o diretório temporário exista
if not os.path.exists(temp_dir):
    os.makedirs(temp_dir)

# Processamento das imagens e anotações
for folder in sorted(os.listdir(base_path)):
    folder_path = os.path.join(base_path, folder)
    image_folder = os.path.join(folder_path, 'images')  # Alterado para o caminho correto de 'images'
    json_file = os.path.join(folder_path, 'result.json')

    if os.path.exists(image_folder) and os.path.exists(json_file):
        with open(json_file, 'r') as f:
            data = json.load(f)

        category_map = {cat['id']: cat['name'] for cat in data['categories']}
        image_id_map = {os.path.basename(img['file_name']).split('\\')[-1]: img['id'] for img in data['images']}

        # Filtrar imagens válidas
        images = [img for img in os.listdir(image_folder) if is_valid_image(img)]

        for image_file in images:
            image_file_og_name = remove_timestamp(image_file)

            if image_file_og_name in processed_images:
                continue
            processed_images.add(image_file_og_name)

            img_path = os.path.join(image_folder, image_file)
            try:
                img = Image.open(img_path)
            except Exception as e:
                print(f"Error opening {img_path}: {e}")
                continue

            image_id = image_id_map.get(image_file)

            if image_id is not None:
                fig = draw_bounding_boxes(img, data['annotations'], image_id, category_map, color_map)

                # Salvar a imagem anotada no diretório temporário
                output_image_path = os.path.join(temp_dir, image_file)
                fig.savefig(output_image_path)
                plt.close(fig)

                # Verificar se a imagem foi salva corretamente
                if os.path.exists(output_image_path):
                    print(f"Imagem salva: {output_image_path}")
                else:
                    print(f"Falha ao salvar a imagem: {output_image_path}")

                total_images_processed += 1
            else:
                print(f"Image {image_file} not found in JSON data")

# Criar o arquivo zip com as imagens anotadas
zip_output_path = '/content/drive/MyDrive/datas/imgtrated.zip'
with zipfile.ZipFile(zip_output_path, 'w') as zipf:
    for root, dirs, files in os.walk(temp_dir):
        for file in files:
            file_path = os.path.join(root, file)
            zipf.write(file_path, os.path.relpath(file_path, temp_dir))

print(f"Total de imagens processadas com bounding boxes: {total_images_processed}")
print(f"Imagens anotadas salvas em: {zip_output_path}")


Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/f42400db-20240815224748000_X60N.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/5f2b7480-20240815224748000_X60.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/edb52bbb-20240815224748000_X60TG.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/5f2afc68-20240815224748000_X1503.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/3b29fdb3-20240815224748000_X1502.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/5af9c3da-20240815224748000_X60IF.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/36e6d93c-20240815224748000_X1501.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/a48fe5b2-20240815224748000_X150N.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/214b55ca-20240815223807000_X1503.jpg
Imagem salva: /content/drive/MyDrive/datas/temp_annotated_images/9b1b62fd-20240815223

In [ ]:
import zipfile
import os
import random
from sklearn.model_selection import train_test_split

# Caminho para o zip e pasta de extração
zip_path = '/content/drive/MyDrive/datas/imgtrated.zip'
extracted_path = '/content/drive/MyDrive/datas/imgtrated/'

# Descompactar o zip
if not os.path.exists(extracted_path):
    os.makedirs(extracted_path)

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extracted_path)

# Listar as imagens extraídas
images = [f for f in os.listdir(extracted_path) if f.endswith('.jpg')]

# Separar 90% para treino e 10% para teste
train_images, test_images = train_test_split(images, test_size=0.1, random_state=42)

print(f'Total de imagens: {len(images)}')
print(f'Imagens para treino: {len(train_images)}')
print(f'Imagens para teste: {len(test_images)}')

# Criar pastas para treino e teste
train_dir = '/content/drive/MyDrive/datas/imgtrated/train/'
test_dir = '/content/drive/MyDrive/datas/imgtrated/test/'

os.makedirs(train_dir, exist_ok=True)
os.makedirs(test_dir, exist_ok=True)

# Mover as imagens para suas respectivas pastas
for image in train_images:
    os.rename(os.path.join(extracted_path, image), os.path.join(train_dir, image))

for image in test_images:
    os.rename(os.path.join(extracted_path, image), os.path.join(test_dir, image))

print("Imagens organizadas em treino e teste.")


Total de imagens: 96
Imagens para treino: 86
Imagens para teste: 10
Imagens organizadas em treino e teste.


In [ ]:
import os
import json
import random
from sklearn.model_selection import train_test_split

# Carregar as anotações
annotations_path = '/content/drive/MyDrive/datas/annotations.json'
with open(annotations_path, 'r') as f:
    annotations = json.load(f)

# Extrair todas as imagens únicas
images = list(set([ann['file_name'] for ann in annotations]))

# Separar 90% para treino e 10% para teste
train_images, test_images = train_test_split(images, test_size=0.1, random_state=42)

# Separar as anotações correspondentes
train_annotations = [ann for ann in annotations if ann['file_name'] in train_images]
test_annotations = [ann for ann in annotations if ann['file_name'] in test_images]

print(f"Total imagens de treino: {len(train_images)}")
print(f"Total imagens de teste: {len(test_images)}")


Total imagens de treino: 124
Total imagens de teste: 14


In [ ]:
import os
import json
import random
from sklearn.model_selection import train_test_split
import tensorflow as tf

# Funções utilitárias para criar TFRecords
def int64_feature(value):
    return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

def bytes_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

def float_list_feature(value):
    return tf.train.Feature(float_list=tf.train.FloatList(value=value))

def bytes_list_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=value))

def int64_list_feature(value):
    return tf.train.Feature(int64_list=tf.train.Int64List(value=value))

# Caminho do arquivo de anotações e das imagens
annotations_path = '/content/drive/MyDrive/datas/annotations.json'
train_image_folder = '/content/drive/MyDrive/datas/imgtrated/train'
test_image_folder = '/content/drive/MyDrive/datas/imgtrated/test'

# Carregar as anotações
with open(annotations_path, 'r') as f:
    annotations = json.load(f)

# Extrair todas as imagens únicas
images = list(set([ann['file_name'] for ann in annotations]))

# Separar 90% para treino e 10% para teste
train_images, test_images = train_test_split(images, test_size=0.1, random_state=42)

# Separar as anotações correspondentes
train_annotations = [ann for ann in annotations if ann['file_name'] in train_images]
test_annotations = [ann for ann in annotations if ann['file_name'] in test_images]

print(f"Total imagens de treino: {len(train_images)}")
print(f"Total imagens de teste: {len(test_images)}")

# Função para criar TFExample
def create_tf_example(annotation, image_folder):
    img_path = os.path.join(image_folder, annotation['file_name'])

    # Verificar se a imagem existe
    if not os.path.exists(img_path):
        print(f"Imagem não encontrada: {img_path}")
        return None

    with tf.io.gfile.GFile(img_path, 'rb') as fid:
        encoded_image_data = fid.read()

    width = annotation['width']
    height = annotation['height']
    filename = annotation['file_name'].encode('utf8')
    image_format = b'jpeg'

    xmins = [annotation['bbox_0'] / width]
    xmaxs = [(annotation['bbox_0'] + annotation['bbox_2']) / width]
    ymins = [annotation['bbox_1'] / height]
    ymaxs = [(annotation['bbox_1'] + annotation['bbox_3']) / height]

    classes_text = [annotation['class_name'].encode('utf8')]
    classes = [annotation['category_id']]

    tf_example = tf.train.Example(features=tf.train.Features(feature={
        'image/height': int64_feature(height),
        'image/width': int64_feature(width),
        'image/filename': bytes_feature(filename),
        'image/source_id': bytes_feature(filename),
        'image/encoded': bytes_feature(encoded_image_data),
        'image/format': bytes_feature(image_format),
        'image/object/bbox/xmin': float_list_feature(xmins),
        'image/object/bbox/xmax': float_list_feature(xmaxs),
        'image/object/bbox/ymin': float_list_feature(ymins),
        'image/object/bbox/ymax': float_list_feature(ymaxs),
        'image/object/class/text': bytes_list_feature(classes_text),
        'image/object/class/label': int64_list_feature(classes),
    }))
    return tf_example

# Função para criar arquivos TFRecord
def create_tfrecord(annotations, record_path, image_folder):
    with tf.io.TFRecordWriter(record_path) as writer:
        for annotation in annotations:
            tf_example = create_tf_example(annotation, image_folder)
            if tf_example is not None:
                writer.write(tf_example.SerializeToString())

# Caminho para salvar os arquivos TFRecord
train_record_path = '/content/drive/MyDrive/datas/tfrecords/train.record'
test_record_path = '/content/drive/MyDrive/datas/tfrecords/test.record'

# Criar o diretório para os TFRecords, se não existir
os.makedirs('/content/drive/MyDrive/datas/tfrecords/', exist_ok=True)

# Chamar a função para criar os arquivos TFRecord
create_tfrecord(train_annotations, train_record_path, train_image_folder)
create_tfrecord(test_annotations, test_record_path, test_image_folder)


Total imagens de treino: 124
Total imagens de teste: 14
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/train/images\5f2b7480-20240815224748000_X60.jpg
Imagem não encontrada: /content/drive/MyDrive/datas/imgtrated/tr

In [ ]:
import os
import tensorflow as tf
from object_detection.utils import dataset_util

def create_tfrecord(annotations, output_path, image_folder):
    # Criar o writer para salvar o arquivo TFRecord
    writer = tf.io.TFRecordWriter(output_path)

    for annotation in annotations:
        # Corrigir o nome do arquivo, caso ele contenha subdiretórios indesejados
        file_name = annotation['file_name'].replace('images/', '').replace('\\', '/')
        image_path = os.path.join(image_folder, file_name)

        # Verificar se o arquivo existe
        if os.path.exists(image_path):
            print(f"Tentando abrir a imagem: {image_path}")
            try:
                # Ler a imagem
                with tf.io.gfile.GFile(image_path, 'rb') as fid:
                    encoded_jpg = fid.read()
            except Exception as e:
                print(f"Erro ao abrir o arquivo {image_path}: {e}")
                continue
        else:
            print(f"Arquivo não encontrado: {image_path}")
            continue

        # Verificar se a anotação possui a chave 'bbox'
        if 'bbox' not in annotation:
            print(f"Anotação sem bounding box, pulando: {annotation}")
            continue

        # Obter as dimensões da imagem
        width = annotation.get('width', 1)  # Definir valor padrão se não encontrado
        height = annotation.get('height', 1)  # Definir valor padrão se não encontrado

        # Coordenadas da bounding box e classes
        xmins = [box[0] / width for box in annotation['bbox']]  # Normalizado
        xmaxs = [box[2] / width for box in annotation['bbox']]
        ymins = [box[1] / height for box in annotation['bbox']]
        ymaxs = [box[3] / height for box in annotation['bbox']]
        classes_text = [cls.encode('utf8') for cls in annotation['classes']]
        classes = [int(cls_id) for cls_id in annotation['classes_id']]

        # Criar o exemplo TFRecord
        tf_example = dataset_util.create_tf_example(
            encoded_jpg, image_path, width, height, xmins, xmaxs, ymins, ymaxs, classes_text, classes
        )
        writer.write(tf_example.SerializeToString())

    writer.close()
    print(f'TFRecord criado com sucesso: {output_path}')

# Chamar a função para criar os arquivos TFRecord
create_tfrecord(train_annotations, '/content/train.record', '/content/drive/MyDrive/datas/imgtrated/train/')
create_tfrecord(test_annotations, '/content/test.record', '/content/drive/MyDrive/datas/imgtrated/test/')


Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
Arquivo não encontrado: /content/drive/MyDrive/datas/imgtrated/train/images/5f2b7480-20240815224748000_X60.jpg
A

In [ ]:
import os
import json

# Defina os caminhos
annotations_path = '/content/drive/MyDrive/datas/annotations.json'
annotation_folder = '/content/drive/MyDrive/datas/imgtrated/train/annotations'  # Pasta para salvar as anotações
os.makedirs(annotation_folder, exist_ok=True)  # Cria a pasta se não existir

# Carregar as anotações
with open(annotations_path, 'r') as f:
    annotations = json.load(f)

# Dicionário para armazenar as anotações
annotations_dict = {}

# Processar cada anotação
for ann in annotations:
    file_name = ann['file_name'].replace('\\', '/')  # Substitui as barras invertidas por barras normais
    class_id = ann['category_id']
    x_min = ann['bbox_0']
    y_min = ann['bbox_1']
    width = ann['bbox_2']
    height = ann['bbox_3']

    # Adicionar a anotação ao dicionário
    if file_name not in annotations_dict:
        annotations_dict[file_name] = []

    annotations_dict[file_name].append({
        'category_id': class_id,
        'bbox_0': x_min,
        'bbox_1': y_min,
        'bbox_2': width,
        'bbox_3': height
    })

# Salvar as anotações no formato YOLO
img_width, img_height = 640, 480  # Defina as dimensões das imagens

def save_annotations(annotations_dict, annotation_folder):
    for file_name, boxes in annotations_dict.items():
        # Obtenha o nome do arquivo sem o caminho, mas com a extensão .txt
        base_file_name = os.path.basename(file_name).replace('.jpg', '.txt')
        txt_file_path = os.path.join(annotation_folder, base_file_name)  # Salvar no diretório de anotações

        with open(txt_file_path, 'w') as f:
            for box in boxes:
                class_id = box['category_id']  # Obtém o class_id
                x_min = box['bbox_0']
                y_min = box['bbox_1']
                width = box['bbox_2']
                height = box['bbox_3']

                # Calcule o centro e normalize para o tamanho da imagem
                x_center = (x_min + (width / 2)) / img_width  # Ajuste para o tamanho da imagem
                y_center = (y_min + (height / 2)) / img_height

                # Normalizar a largura e altura
                norm_width = width / img_width
                norm_height = height / img_height

                # Escreva a linha no arquivo .txt
                f.write(f"{class_id} {x_center} {y_center} {norm_width} {norm_height}\n")

# Salvar as anotações
save_annotations(annotations_dict, annotation_folder)


In [ ]:
import cv2
import numpy as np
import os
import json
train_image_folder = '/content/drive/MyDrive/datas/imgtrated/train'  # Caminho para imagens de treino
annotation_folder = '/content/drive/MyDrive/datas/imgtrated/train/annotations'  # Caminho para anotações
def load_data(image_folder, annotation_folder):
    images = []
    annotations = []
    for image_name in os.listdir(image_folder):
        if image_name.endswith('.jpg'):
            img = cv2.imread(os.path.join(image_folder, image_name))
            img = cv2.resize(img, (416, 416))  # Ajuste o tamanho para 416x416
            images.append(img)

            # Carregar as anotações correspondentes
            annotation_path = os.path.join(annotation_folder, image_name.replace('.jpg', '.txt'))
            if os.path.exists(annotation_path):
                with open(annotation_path, 'r') as f:
                    annotations.append(f.readlines())
    return np.array(images), annotations

X_train, y_train = load_data(train_image_folder, annotation_folder)


In [ ]:
# Importar bibliotecas necessárias
import numpy as np
import os
import json
import cv2
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

# Defina os caminhos
annotations_path = '/content/drive/MyDrive/datas/annotations.json'
train_image_folder = '/content/drive/MyDrive/datas/imgtrated/train'
test_image_folder = '/content/drive/MyDrive/datas/imgtrated/test'

def load_data(image_folder, annotations_path):
    with open(annotations_path, 'r') as f:
        annotations = json.load(f)

    images = []
    labels = []

    for entry in annotations:
        # Extrair apenas o nome do arquivo, removendo a parte 'images\\'
        file_name = entry['file_name'].replace('images\\', '')  # Remove 'images\\'
        print(f"Carregando: {file_name}")  # Para depuração

        # Montando o caminho correto para a imagem
        image_path = os.path.join(image_folder, file_name)

        # Normaliza os separadores de caminho para o formato Unix
        image_path = image_path.replace('\\', '/')

        # Verificar se a imagem existe e carregá-la
        img = cv2.imread(image_path)

        if img is None:
            continue  # Pule para a próxima imagem se houver erro

        img = cv2.resize(img, (224, 224))  # Redimensionar para o tamanho que seu modelo espera
        images.append(img)

        # Mapear category_id para os rótulos
        labels.append(entry['category_id'])  # ou mapeie conforme necessário

    return np.array(images), np.array(labels)

# Carregar dados de treinamento
X_train, y_train = load_data(train_image_folder, annotations_path)

# Normalizar os dados
X_train = X_train / 255.0  # Normaliza os valores de pixel entre 0 e 1

# Verificar se os dados foram carregados corretamente
print(f"Número de amostras em X_train: {len(X_train)}")
print(f"Número de rótulos em y_train: {len(y_train)}")

if len(X_train) > 0 and len(y_train) > 0:
    # Dividir os dados em treinamento e validação (opcional)
    from sklearn.model_selection import train_test_split
    X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42)
else:
    print("Erro: Não há dados suficientes para dividir em treinamento e validação.")

# Criar o modelo
model = keras.Sequential([
    layers.Input(shape=(224, 224, 3)),  # Entrada para imagens RGB 224x224
    layers.Conv2D(32, (3, 3), activation='relu'),
    layers.MaxPooling2D(pool_size=(2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D(pool_size=(2, 2)),
    layers.Flatten(),
    layers.Dense(128, activation='relu'),
    layers.Dense(len(np.unique(y_train)), activation='softmax')  # O número de classes deve ser igual ao número de categorias
])

# Compilar o modelo
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Treinar o modelo
history = model.fit(X_train, y_train, validation_data=(X_val, y_val), epochs=10, batch_size=32)

# Avaliar o modelo
test_images, test_labels = load_data(test_image_folder, annotations_path)  # Carregue suas imagens de teste
test_images = test_images / 255.0  # Normalizar
loss, accuracy = model.evaluate(test_images, test_labels)
print(f'Test Accuracy: {accuracy:.2f}')


A saída de streaming foi truncada nas últimas 5000 linhas.
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X150N.jpg
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X150N.jpg
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X150N.jpg
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X150N.jpg
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X150N.jpg
Erro ao carregar a imagem: /content/drive/MyDrive/datas/imgtrated/train/732005ea-20240812184522000_X150N.jpg
Carregando: 732005ea-20240812184522000_X15

In [ ]:
# Importar bibliotecas necessárias
import numpy as np
import os
import json
import cv2
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from sklearn.metrics import precision_score, recall_score, f1_score

# Defina os caminhos
annotations_path = '/content/drive/MyDrive/datas/annotations.json'
train_image_folder = '/content/drive/MyDrive/datas/imgtrated/train'
test_image_folder = '/content/drive/MyDrive/datas/imgtrated/test'

# Função para carregar dados
def load_data(image_folder, annotations_path):
    with open(annotations_path, 'r') as f:
        annotations = json.load(f)

    images = []
    labels = []
    boxes = []

    for entry in annotations:
        # Extrair o nome do arquivo removendo 'images\\'
        file_name = entry['file_name'].replace('images\\', '')
        image_path = os.path.join(image_folder, file_name).replace('\\', '/')

        img = cv2.imread(image_path)
        if img is None:
            continue
        img = cv2.resize(img, (224, 224))
        images.append(img)

        # Adiciona os rótulos e bounding boxes
        labels.append(entry['category_id'])
        boxes.append([entry['bbox_0'], entry['bbox_1'], entry['bbox_2'], entry['bbox_3']])

    return np.array(images), np.array(labels), np.array(boxes)

# Carregar os dados de treinamento
X_train, y_train, boxes_train = load_data(train_image_folder, annotations_path)
X_train = X_train / 255.0  # Normalização

# Dividir os dados em treinamento e validação
from sklearn.model_selection import train_test_split
X_train, X_val, y_train, y_val, boxes_train, boxes_val = train_test_split(
    X_train, y_train, boxes_train, test_size=0.2, random_state=42)

# Modelo de detecção de objetos
inputs = keras.Input(shape=(224, 224, 3))
x = layers.Conv2D(32, (3, 3), activation='relu')(inputs)
x = layers.MaxPooling2D(pool_size=(2, 2))(x)
x = layers.Conv2D(64, (3, 3), activation='relu')(x)
x = layers.MaxPooling2D(pool_size=(2, 2))(x)
x = layers.Flatten()(x)

# Saída para classificação de objetos
class_output = layers.Dense(128, activation='relu')(x)
class_output = layers.Dense(len(np.unique(y_train)), activation='softmax', name='class_output')(class_output)

# Saída para detecção de bounding boxes
bbox_output = layers.Dense(128, activation='relu')(x)
bbox_output = layers.Dense(4, activation='linear', name='bbox_output')(bbox_output)

# Modelo com duas saídas
model = keras.Model(inputs=inputs, outputs=[class_output, bbox_output])

# Compilar o modelo
model.compile(optimizer='adam',
              loss={'class_output': 'sparse_categorical_crossentropy', 'bbox_output': 'mse'},
              metrics={'class_output': 'accuracy', 'bbox_output': 'mse'})

# Treinar o modelo com métricas de validação
history = model.fit(X_train, {'class_output': y_train, 'bbox_output': boxes_train},
                    validation_data=(X_val, {'class_output': y_val, 'bbox_output': boxes_val}),
                    epochs=10, batch_size=32)

# Avaliar o modelo
X_test, y_test, boxes_test = load_data(test_image_folder, annotations_path)
X_test = X_test / 255.0

# Avaliação final no conjunto de teste
losses = model.evaluate(X_test, {'class_output': y_test, 'bbox_output': boxes_test})

# Extração das métricas específicas
total_loss, class_output_accuracy, bbox_output_mse = losses[0], losses[1], losses[2]
print(f'Total Loss: {total_loss:.4f}')
print(f'Test Class Output Accuracy: {class_output_accuracy:.4f}')
print(f'Test BBox Output MSE: {bbox_output_mse:.4f}')

# Previsões no conjunto de validação para métricas adicionais
y_val_pred, boxes_val_pred = model.predict(X_val)
y_val_pred_labels = np.argmax(y_val_pred, axis=1)

# Cálculo das métricas de validação
precision = precision_score(y_val, y_val_pred_labels, average='weighted')
recall = recall_score(y_val, y_val_pred_labels, average='weighted')
f1 = f1_score(y_val, y_val_pred_labels, average='weighted')

print(f'Validation Precision: {precision:.4f}')
print(f'Validation Recall: {recall:.4f}')
print(f'Validation F1-Score: {f1:.4f}')

# Salvando o modelo
model.save('object_detection_model.keras')


Epoch 1/10
38/38 ━━━━━━━━━━━━━━━━━━━━ 148s 4s/step - bbox_output_mse: 20858.2285 - class_output_accuracy: 0.3969 - loss: 20870.3184 - val_bbox_output_mse: 12123.1582 - val_class_output_accuracy: 0.5084 - val_loss: 12124.2295
Epoch 2/10
38/38 ━━━━━━━━━━━━━━━━━━━━ 199s 4s/step - bbox_output_mse: 12356.6367 - class_output_accuracy: 0.4669 - loss: 12358.0488 - val_bbox_output_mse: 12167.3486 - val_class_output_accuracy: 0.3367 - val_loss: 12168.8359
Epoch 3/10
38/38 ━━━━━━━━━━━━━━━━━━━━ 202s 4s/step - bbox_output_mse: 12205.4785 - class_output_accuracy: 0.4252 - loss: 12206.9902 - val_bbox_output_mse: 12282.1250 - val_class_output_accuracy: 0.5758 - val_loss: 12283.0635
Epoch 4/10
38/38 ━━━━━━━━━━━━━━━━━━━━ 143s 4s/step - bbox_output_mse: 12439.7871 - class_output_accuracy: 0.6012 - loss: 12440.6748 - val_bbox_output_mse: 12152.1318 - val_class_output_accuracy: 0.5084 - val_loss: 12153.2236
Epoch 5/10
38/38 ━━━━━━━━━━━━━━━━━━━━ 200s 4s/step - bbox_output_mse: 12456.8662 - class_output_accu

In [ ]:
import os
import zipfile

# Caminhos das pastas
source_folder = '/content/drive/MyDrive/datas/imgtrated/train'
output_folder = '/content/drive/MyDrive/datas'
output_zip = os.path.join(output_folder, 'train_images.zip')

# Função para zipar arquivos
def zip_images(source_folder, output_zip):
    with zipfile.ZipFile(output_zip, 'w') as zipf:
        for foldername, subfolders, filenames in os.walk(source_folder):
            for filename in filenames:
                # Caminho completo do arquivo
                file_path = os.path.join(foldername, filename)
                # Adicionar o arquivo ao zip
                zipf.write(file_path, os.path.relpath(file_path, source_folder))
    print(f'Imagens zipadas com sucesso em {output_zip}')

# Executar a função
zip_images(source_folder, output_zip)


Imagens zipadas com sucesso em /content/drive/MyDrive/datas/train_images.zip
